# Introduction/Business Problem

Houston is the forth biggest city in U.S. and has been a place growing in population and business in the past few decades. With such a quick expansion, Houston is definitely one the most fast-growing city in the U.S. The growing city comes with increasing population and comercial activitis and one of them is coffee drinking. Coffee shops have turned into a place for people to chill out or to have some informal business meeting or social events. Therefore, how the coffee shop interact with its nearby neighborhood is quite an interesting question. In this study, I will explore the Houston neighborhood, discuss the interaction between different venues and the coffee shops and then conclude on where is a reasonable place to run a coffee shop in Houston.

##### Business problem
Where to run a coffee shop in Houston? I will discuss on the Houston neighborhoods and demonstrate where would be an ideal place to run a coffee shop in Houston based on the available data.
##### Target Audience
People interested in opening a coffee shop in one of Houston neighborhood would be the target audience for this study.

# Data

## Data used in this study

In this study Foursquare spatial data would be used to explore the venues in Houston neighborhoods and the demographic data of each neighborhood would be analyzed. Foursquare (https://foursquare.com/) currently has the most comprehensive location dataset and quite accurate and the data can be acquired through API. Many popular services like Apple Maps, Uber, Snapchat and Twitter use their location data. It collects data from users to add or complete the information, which is the crowd-sourced data and it keeps growing while more and more people use their service. To acquire the data, two queries need to be specified: what to find and where to find. In this study, the Houston neighborhood data was acquired from Wikipedia (https://en.wikipedia.org/wiki/List_of_Houston_neighborhoods), which contains nine location and 88 neighborhoods. The 2017 demographic data of Houston neighborhood was used in this study and was acquired from city of Houston website (https://www.houstontx.gov/planning/Demographics/) including total population, persons per square mile, median household income (USD) and median housing value (USD). The geojson data of Houston neighborhoods was acquired from GitHub portal (https://github.com/blackmad/neighborhoods).

In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files
 
!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Solving environment: done

## Package Plan ##

  environment location: /opt/anaconda3

  added / updated specs:
    - geopy


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    ca-certificates-2021.5.30  |       h033912b_0         136 KB  conda-forge
    certifi-2021.5.30          |   py38h50d1736_0         141 KB  conda-forge
    conda-4.10.3               |   py38h50d1736_2         3.1 MB  conda-forge
    geographiclib-1.52         |     pyhd8ed1ab_0          35 KB  conda-forge
    geopy-2.2.0                |     pyhd8ed1ab_0          67 KB  conda-forge
    openssl-1.1.1l             |       h0d85af4_0         1.9 MB  conda-forge
    ------------------------------------------------------------
                                           Total:         5.3 MB

The following NEW packages will be INSTALLED:

  geographiclib      conda-forge/noarch::geographiclib-1.52-pyhd8ed1ab_0
  geopy    

## 1. Download and Explore Dataset
### Acquire data from Wikipedia page
Neighborhood Data: Wikipedia https://en.wikipedia.org/wiki/List_of_Houston_neighborhoods

In [5]:
from bs4 import BeautifulSoup

In [7]:
html_doc='List of Houston neighborhoods - Wikipedia.htm'
with open(html_doc) as html_file:
    soup = BeautifulSoup(html_file, 'html.parser')
#print(soup.prettify())

In [8]:
data=[]
for lines in soup.find_all('td'):
    data.append(lines.text)
#print(data)

In [9]:
print(data.index('Lawndale / Wayside\n'))
print(len(data))

349
419


In [10]:
#### Keep the needed data
del data[352:419]
print(len(data))

352


In [11]:
##### Create list for Location and Neighborhood
Location=[]
Neighborhood=[]
for i in range(len(data)):
    if i%4==1:
        Neighborhood.append(data[i].strip('\n'))
    elif i%4==2:
        Location.append(data[i].strip('\n'))
    
Neighborhood[0:10]

['Willowbrook',
 'Greater Greenspoint',
 'Carverdale',
 'Fairbanks / Northwest Crossing',
 'Greater Inwood',
 'Acres Home',
 'Hidden Valley',
 'Westbranch',
 'Addicks / Park Ten',
 'Spring Branch West']

In [12]:
df_Houston = pd.DataFrame(
    {'Location': Location, 'Neighborhood': Neighborhood})
df_Houston.sort_values(['Neighborhood'], ascending=True, inplace=True)
df_Houston.head()

Location             Neighborhood
5   Northwest               Acres Home
8        West       Addicks / Park Ten
22       West  Afton Oaks / River Oaks
24  Southwest                    Alief
33      South           Astrodome Area

In [13]:
##### Write Neighborhood data to Houston Neighborhoods.csv and then manually copy and paste the demographic data from PDF files. 
df_Houston.to_csv('Houston Neighborhoods')

In [14]:
Demographic=pd.read_csv('Houston_neighborhood_demographic.csv')
Demographic.drop(['Unnamed: 8','Unnamed: 9','Unnamed: 10'], inplace=True, axis=1)
Demographic['Persons per Square Mile'].astype("float64")
Demographic.head()

Location             Neighborhood   Latitude  Longitude  Total Population  \
0  Northwest               Acres Home  29.870715 -95.436558           25846.0   
1       West       Addicks / Park Ten  29.813269 -95.645476           20694.0   
2       West  Afton Oaks / River Oaks  29.747474 -95.433124           14875.0   
3  Southwest                    Alief  29.682815 -95.593005          119598.0   
4      South           Astrodome Area  29.685404 -95.403244           17944.0   

   Persons per Square Mile  Median Household Income (USD)  \
0                   2885.0                        41358.0   
1                    883.0                        82869.0   
2                   4119.0                       152092.0   
3                   8106.0                        42928.0   
4                   5646.0                        51510.0   

   Median Housing Value (USD)  
0                    134810.0  
1                    221710.0  
2                   1203824.0  
3                    100590.0  
4                    126921.0

In [15]:
#### Check geojson data
import json
with open ('houston_geo.json') as json_file:
    houston_geo=json.load(json_file)

name=[]
for i in range(len(houston_geo['features'])):
    name.append(houston_geo['features'][i]['properties']['name'])
name.sort()
#name

In [16]:
#### Match the Neighborhood name in Demographic with houston_geo.json

for i in range(len(name)):
    if name[i] != Demographic['Neighborhood'][i]:
        Demographic['Neighborhood'][i]=name[i]


<ipython-input-16-6ae8a3609d1c>:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  Demographic['Neighborhood'][i]=name[i]


In [17]:
print('The dataframe has {} Location and {} Neighborhoods.'.format(
        len(Demographic['Location'].unique()),
        Demographic.shape[0]
    )
)

The dataframe has 9 Location and 88 Neighborhoods.


## Get the top 100 venues that are in each Houston neighborhood within a radius of 2000 meters

#### Define Foursquare Credentials and Version

In [18]:
CLIENT_ID = 'JDCIUT3B1CNOV0WPN4UD1NI11MIU5EPDWNAVBDBGMHKVVKW2' # your Foursquare ID
CLIENT_SECRET = 'ZSSF3VIB2TWEXKLZMWLQCACIFKU5TTWJTWOTO4L20BMB2OOW' # your Foursquare Secret
VERSION = '20190812'

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: JDCIUT3B1CNOV0WPN4UD1NI11MIU5EPDWNAVBDBGMHKVVKW2
CLIENT_SECRET:ZSSF3VIB2TWEXKLZMWLQCACIFKU5TTWJTWOTO4L20BMB2OOW


In [19]:
#####Create a function to download venues data from Foursquare and extract category repeatly for all the neighborhoods in Houston
def getNearbyVenues(names, latitudes, longitudes, radius=2000, LIMIT = 100):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [20]:
#### Create a new dataframe
Houston_venues = getNearbyVenues(names=Demographic['Neighborhood'],
                                   latitudes=Demographic['Latitude'],
                                   longitudes=Demographic['Longitude']
                                  )

Acres Home
Addicks Park Ten
Afton Oaks / River Oaks Area
Alief
Astrodome Area
Braeburn
Braeswood Place
Brays Oaks
Briarforest Area
Carverdale
Central Northwest
Central Southwest
Clear Lake
Clinton Park Tri-Community
Denver Harbor / Port Houston
Downtown
East Houston
East Little York / Homestead
Eastex - Jensen Area
Edgebrook Area
El Dorado / Oates Prairie
Eldridge / West Oaks
Fairbanks / Northwest Crossing
Fondren Gardens
Fort Bend / Houston
Fourth Ward
Golfcrest / Bellfort / Reveille
Greater Eastwood
Greater Fifth Ward
Greater Greenspoint
Greater Heights
Greater Hobby Area
Greater Inwood
Greater Third Ward
Greater Uptown
Greenway / Upper Kirby Area
Gulfgate Riverview / Pine Valley
Gulfton
Harrisburg / Manchester
Hidden Valley
Hunterwood
Iah / Airport Area
Independence Heights
Kashmere Gardens
Kingwood Area
Lake Houston
Langwood
Lawndale / Wayside
Lazy Brook / Timbergrove
Macgregor
Magnolia Park
Meadowbrook / Allendale
Medical Center Area
Memorial
Meyerland Area
Mid West
Midtown
Minnet

In [21]:
print(Houston_venues.shape)
Houston_venues.head()

(5107, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0   Acres Home              29.870715              -95.436558   
1   Acres Home              29.870715              -95.436558   
2   Acres Home              29.870715              -95.436558   
3   Acres Home              29.870715              -95.436558   
4   Acres Home              29.870715              -95.436558   

                                    Venue  Venue Latitude  Venue Longitude  \
0             Burns Orginal BBQ Est. 1973       29.876950       -95.420984   
1                           Family Dollar       29.872253       -95.437729   
2                   Sylvester Turner Park       29.865159       -95.452752   
3                              Vera Steel       29.861840       -95.442030   
4  Houston Astros MLB Urban Youth Academy       29.869973       -95.452752   

               Venue Category  
0                   BBQ Joint  
1              Discount Store  
2                        Park  
3  Construction & Landscaping  
4              Baseball Field

In [22]:
#### Find unique categories
print('There are {} uniques categories.'.format(len(Houston_venues['Venue Category'].unique())))

There are 333 uniques categories.


# Methodology 

## Explore Neighborhood in Houston

In [23]:
# one hot encoding
Houston_onehot = pd.get_dummies(Houston_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
Houston_onehot['Neighborhood Name'] = Houston_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [Houston_onehot.columns[-1]] + list(Houston_onehot.columns[:-1])
Houston_onehot = Houston_onehot[fixed_columns]

Houston_onehot.head()

Neighborhood Name  ATM  Accessories Store  Advertising Agency  \
0        Acres Home    0                  0                   0   
1        Acres Home    0                  0                   0   
2        Acres Home    0                  0                   0   
3        Acres Home    0                  0                   0   
4        Acres Home    0                  0                   0   

   Afghan Restaurant  African Restaurant  Airport  Airport Lounge  \
0                  0                   0        0               0   
1                  0                   0        0               0   
2                  0                   0        0               0   
3                  0                   0        0               0   
4                  0                   0        0               0   

   Airport Service  Airport Terminal  American Restaurant  Animal Shelter  \
0                0                 0                    0               0   
1                0                 0                    0               0   
2                0                 0                    0               0   
3                0                 0                    0               0   
4                0                 0                    0               0   

   Antique Shop  Arcade  Argentinian Restaurant  Art Gallery  Art Museum  \
0             0       0                       0            0           0   
1             0       0                       0            0           0   
2             0       0                       0            0           0   
3             0       0                       0            0           0   
4             0       0                       0            0           0   

   Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  \
0                    0                     0                 0   
1                    0                     0                 0   
2                    0                     0                 0   
3                    0                     0                 0   
4                    0                     0                 0   

   Athletics & Sports  Auto Garage  Auto Workshop  Automotive Shop  BBQ Joint  \
0                   0            0              0                0          1   
1                   0            0              0                0          0   
2                   0            0              0                0          0   
3                   0            0              0                0          0   
4                   0            0              0                0          0   

   Baby Store  Bagel Shop  Bakery  Bank  Bar  Baseball Field  \
0           0           0       0     0    0               0   
1           0           0       0     0    0               0   
2           0           0       0     0    0               0   
3           0           0       0     0    0               0   
4           0           0       0     0    0               1   

   Baseball Stadium  Basketball Court  Basketball Stadium  Bay  Beach  \
0                 0                 0                   0    0      0   
1                 0                 0                   0    0      0   
2                 0                 0                   0    0      0   
3                 0                 0                   0    0      0   
4                 0                 0                   0    0      0   

   Beer Bar  Beer Garden  Beer Store  Big Box Store  Bike Shop  Bike Trail  \
0         0            0           0              0          0           0   
1         0            0           0              0          0           0   
2         0            0           0              0          0           0   
3         0            0           0              0          0           0   
4         0            0           0              0          0           0   

   Bistro  Boat or Ferry  Bookstore  Botanical Garden  Boutique  \
0       0           

In [24]:
### Dataframe size
Houston_onehot.shape

(5107, 334)

#### Group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [25]:
Houston_grouped = Houston_onehot.groupby('Neighborhood Name').mean().reset_index()
Houston_grouped.head()

Neighborhood Name  ATM  Accessories Store  Advertising Agency  \
0                    Acres Home  0.0                0.0                 0.0   
1              Addicks Park Ten  0.0                0.0                 0.0   
2  Afton Oaks / River Oaks Area  0.0                0.0                 0.0   
3                         Alief  0.0                0.0                 0.0   
4                Astrodome Area  0.0                0.0                 0.0   

   Afghan Restaurant  African Restaurant  Airport  Airport Lounge  \
0                0.0                 0.0      0.0             0.0   
1                0.0                 0.0      0.0             0.0   
2                0.0                 0.0      0.0             0.0   
3                0.0                 0.0      0.0             0.0   
4                0.0                 0.0      0.0             0.0   

   Airport Service  Airport Terminal  American Restaurant  Animal Shelter  \
0              0.0               0.0             0.000000             0.0   
1              0.0               0.0             0.000000             0.0   
2              0.0               0.0             0.010000             0.0   
3              0.0               0.0             0.022727             0.0   
4              0.0               0.0             0.010000             0.0   

   Antique Shop  Arcade  Argentinian Restaurant  Art Gallery  Art Museum  \
0           0.0     0.0                     0.0          0.0        0.00   
1           0.0     0.0                     0.0          0.0        0.00   
2           0.0     0.0                     0.0          0.0        0.01   
3           0.0     0.0                     0.0          0.0        0.00   
4           0.0     0.0                     0.0          0.0        0.00   

   Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  \
0                  0.0                   0.0          0.000000   
1                  0.0                   0.0          0.000000   
2                  0.0                   0.0          0.000000   
3                  0.0                   0.0          0.022727   
4                  0.0                   0.0          0.000000   

   Athletics & Sports  Auto Garage  Auto Workshop  Automotive Shop  BBQ Joint  \
0                 0.0          0.0            0.0              0.0       0.20   
1                 0.0          0.0            0.0              0.0       0.00   
2                 0.0          0.0            0.0              0.0       0.00   
3                 0.0          0.0            0.0              0.0       0.00   
4                 0.0          0.0            0.0              0.0       0.03   

   Baby Store  Bagel Shop  Bakery  Bank   Bar  Baseball Field  \
0         0.0         0.0    0.00  0.00  0.00             0.2   
1         0.0         0.0    0.00  0.00  0.00             0.0   
2         0.0         0.0    0.01  0.00  0.02             0.0   
3         0.0         0.0    0.00  0.00  0.00             0.0   
4         0.0         0.0    0.01  0.01  0.02             0.0   

   Baseball Stadium  Basketball Court  Basketball Stadium  Bay  Beach  \
0               0.0               0.0                 0.0  0.0    0.0   
1               0.0               0.0                 0.0  0.0    0.0   
2               0.0               0.0                 0.0  0.0    0.0   
3               0.0               0.0                 0.0  0.0    0.0   
4               0.0               0.0                 0.0  0.0    0.0   

   Beer Bar  Beer Garden  Beer Store  Big Box Store  Bike Shop  Bike Trail  \
0       0.0          0.0         0.0           0.00        0.0         0.0   
1       0.0          0.0         0.0           0.00        0.0         0.0   
2       0.0          0.0         0.0           0.00        0.0         0.0   
3       0.0          0.0         0.0           0.00        0.0         0.0   
4       0.0          0.0         0.0           0.01        0.0         0.0   

   Bistro  Boat or Fe

In [26]:
### Dataframe size
Houston_grouped.shape

(88, 334)

#### Print each neighborhood along with the top 5 most common venues

In [27]:
num_top_venues = 5

for hood in Houston_grouped['Neighborhood Name']:
    print("----"+hood+"----")
    temp = Houston_grouped[Houston_grouped['Neighborhood Name'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Acres Home----
                        venue  freq
0  Construction & Landscaping   0.2
1                        Park   0.2
2              Baseball Field   0.2
3              Discount Store   0.2
4                   BBQ Joint   0.2


----Addicks Park Ten----
                   venue  freq
0      Indian Restaurant  0.25
1    Government Building  0.25
2                Dog Run  0.25
3  Outdoors & Recreation  0.25
4   Other Great Outdoors  0.00


----Afton Oaks / River Oaks Area----
                     venue  freq
0  New American Restaurant  0.06
1   Furniture / Home Store  0.06
2                     Café  0.04
3       Mexican Restaurant  0.04
4         Sushi Restaurant  0.04


----Alief----
                  venue  freq
0  Fast Food Restaurant  0.11
1           Pizza Place  0.07
2         Grocery Store  0.07
3        Discount Store  0.07
4     Mobile Phone Shop  0.05


----Astrodome Area----
                venue  freq
0      Sandwich Place  0.05
1   Mobile Phone Shop  0.05
2         

            venue  freq
0     Zoo Exhibit  0.09
1             Bar  0.08
2     Coffee Shop  0.06
3  Science Museum  0.04
4           Trail  0.04


----Northshore----
                venue  freq
0         Coffee Shop  0.07
1                 Bar  0.04
2  Mexican Restaurant  0.04
3  Italian Restaurant  0.04
4                Café  0.03


----Northside Village----
                  venue  freq
0    Mexican Restaurant  0.11
1  Fast Food Restaurant  0.08
2        Discount Store  0.06
3     Convenience Store  0.05
4        Sandwich Place  0.05


----Northside/Northline----
                    venue  freq
0    Fast Food Restaurant  0.07
1  Furniture / Home Store  0.05
2          Sandwich Place  0.05
3          Discount Store  0.05
4     Fried Chicken Joint  0.05


----Ost / South Union----
                  venue  freq
0    Mexican Restaurant  0.20
1        Discount Store  0.05
2           Video Store  0.04
3        Sandwich Place  0.04
4  Fast Food Restaurant  0.04


----Park Place----
        

#### Put into a *pandas* dataframe

In [28]:
#### First, write a function to sort the venues in descending order.
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [80]:
#### Create a new dataframe and display the top 8 venues for each neighborhood.
num_top_venues = 8

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood Name']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood Name'] = Houston_grouped['Neighborhood Name']

for ind in np.arange(Houston_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(Houston_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood Name       1st Most Common Venue  \
0                    Acres Home  Construction & Landscaping   
1              Addicks Park Ten           Indian Restaurant   
2  Afton Oaks / River Oaks Area     New American Restaurant   
3                         Alief        Fast Food Restaurant   
4                Astrodome Area              Sandwich Place   

    2nd Most Common Venue 3rd Most Common Venue  4th Most Common Venue  \
0                    Park        Baseball Field         Discount Store   
1     Government Building               Dog Run  Outdoors & Recreation   
2  Furniture / Home Store                  Café     Mexican Restaurant   
3             Pizza Place         Grocery Store         Discount Store   
4       Mobile Phone Shop           Pizza Place     Mexican Restaurant   

  5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0             BBQ Joint                   ATM     Outdoor Sculpture   
1  Other Great Outdoors  Pakistani Restaurant       Paintball Field   
2      Sushi Restaurant                   Gym          Burger Joint   
3     Mobile Phone Shop           Video Store        Cosmetics Shop   
4           Coffee Shop         Grocery Store                 Hotel   

           8th Most Common Venue  
0  Paper / Office Supplies Store  
1           Outdoor Supply Store  
2             Italian Restaurant  
3                    Golf Course  
4                     Food Truck

In [81]:
neighborhoods_venues_sorted.shape

(88, 9)

 ## Cluster Neighborhoods

In [104]:
#### Run kmeans to cluster the neighborhood into 8 clusters.

# set number of clusters
kclusters = 8

Houston_grouped_clustering = Houston_grouped.drop('Neighborhood Name', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(Houston_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_

array([1, 0, 2, 3, 2, 5, 5, 3, 2, 5, 5, 3, 2, 5, 5, 2, 3, 3, 3, 5, 5, 2,
       2, 3, 1, 2, 5, 2, 3, 5, 2, 5, 3, 3, 2, 2, 2, 3, 2, 6, 3, 5, 5, 2,
       3, 2, 4, 5, 5, 2, 3, 5, 3, 2, 2, 2, 2, 2, 7, 2, 2, 5, 3, 5, 5, 5,
       5, 5, 3, 5, 7, 5, 5, 3, 5, 5, 5, 2, 3, 3, 2, 2, 5, 3, 2, 5, 5, 2],
      dtype=int32)

In [90]:
#### Create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.

# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

Houston_merged = Demographic[['Location', 'Neighborhood', 'Latitude', 'Longitude']]

# merge Houston_grouped with toronto_data to add latitude/longitude for each neighborhood
Houston_merged = Houston_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood Name'), on='Neighborhood')

Houston_merged.head() # check the last columns!

Location                  Neighborhood   Latitude  Longitude  \
0  Northwest                    Acres Home  29.870715 -95.436558   
1       West              Addicks Park Ten  29.813269 -95.645476   
2       West  Afton Oaks / River Oaks Area  29.747474 -95.433124   
3  Southwest                         Alief  29.682815 -95.593005   
4      South                Astrodome Area  29.685404 -95.403244   

   Cluster Labels       1st Most Common Venue   2nd Most Common Venue  \
0               1  Construction & Landscaping                    Park   
1               0           Indian Restaurant     Government Building   
2               2     New American Restaurant  Furniture / Home Store   
3               3        Fast Food Restaurant             Pizza Place   
4               2              Sandwich Place       Mobile Phone Shop   

  3rd Most Common Venue  4th Most Common Venue 5th Most Common Venue  \
0        Baseball Field         Discount Store             BBQ Joint   
1               Dog Run  Outdoors & Recreation  Other Great Outdoors   
2                  Café     Mexican Restaurant      Sushi Restaurant   
3         Grocery Store         Discount Store     Mobile Phone Shop   
4           Pizza Place     Mexican Restaurant           Coffee Shop   

  6th Most Common Venue 7th Most Common Venue          8th Most Common Venue  
0                   ATM     Outdoor Sculpture  Paper / Office Supplies Store  
1  Pakistani Restaurant       Paintball Field           Outdoor Supply Store  
2                   Gym          Burger Joint             Italian Restaurant  
3           Video Store        Cosmetics Shop                    Golf Course  
4         Grocery Store                 Hotel                     Food Truck

In [91]:
# create map
map_clusters = folium.Map(location=[29.8, -95.3676974], zoom_start=10)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(Houston_merged['Latitude'], Houston_merged['Longitude'], Houston_merged['Neighborhood'], Houston_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=3,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

# Results
#### Examine each cluster and determine the discriminating venue categories that distinguish each cluster. Based on the defining categories, and then assign a name to each cluster.

## Cluster 0

In [92]:
Houston_merged.loc[Houston_merged['Cluster Labels'] == 0, Houston_merged.columns[[1] + list(range(5, Houston_merged.shape[1]))]]


Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
1  Addicks Park Ten     Indian Restaurant   Government Building   

  3rd Most Common Venue  4th Most Common Venue 5th Most Common Venue  \
1               Dog Run  Outdoors & Recreation  Other Great Outdoors   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  
1  Pakistani Restaurant       Paintball Field  Outdoor Supply Store

## Cluster 1

In [93]:
Houston_merged.loc[Houston_merged['Cluster Labels'] == 1, Houston_merged.columns[[1] + list(range(5, Houston_merged.shape[1]))]]


Neighborhood       1st Most Common Venue 2nd Most Common Venue  \
0            Acres Home  Construction & Landscaping                  Park   
24  Fort Bend / Houston           Convenience Store                 Hotel   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0         Baseball Field        Discount Store             BBQ Joint   
24            Food Truck    Seafood Restaurant        Discount Store   

      6th Most Common Venue 7th Most Common Venue  \
0                       ATM     Outdoor Sculpture   
24  Health & Beauty Service                  Park   

            8th Most Common Venue  
0   Paper / Office Supplies Store  
24     Construction & Landscaping

## Cluster 2

In [94]:
Houston_merged.loc[Houston_merged['Cluster Labels'] == 2, Houston_merged.columns[[1] + list(range(5, Houston_merged.shape[1]))]]


Neighborhood      1st Most Common Venue  \
2                  Afton Oaks / River Oaks Area    New American Restaurant   
4                                Astrodome Area             Sandwich Place   
8                              Briarforest Area             Sandwich Place   
12                                   Clear Lake                Pizza Place   
15                                     Downtown                      Hotel   
21                         Eldridge / West Oaks             Sandwich Place   
22               Fairbanks / Northwest Crossing          Mobile Phone Shop   
25                                  Fourth Ward                        Bar   
27                             Greater Eastwood                        Bar   
30                              Greater Heights         Mexican Restaurant   
34                               Greater Uptown                Coffee Shop   
35                  Greenway / Upper Kirby Area                      Hotel   
36             Gulfgate Riverview / Pine Valley               Burger Joint   
38                      Harrisburg / Manchester          Indian Restaurant   
43                             Kashmere Gardens                Coffee Shop   
45                                 Lake Houston       Fast Food Restaurant   
49                                    Macgregor         Mexican Restaurant   
53                                     Memorial                Zoo Exhibit   
54                               Meyerland Area         Mexican Restaurant   
55                                     Mid West           Department Store   
56                                      Midtown  Middle Eastern Restaurant   
57                                     Minnetex                Coffee Shop   
59                          Neartown - Montrose                Zoo Exhibit   
60                                   Northshore                Coffee Shop   
77                           Spring Branch West             Clothing Store   
80                             University Place                Coffee Shop   
81  Washington Avenue Coalition / Memorial Park                       Park   
84                                    Westchase             Sandwich Place   
87                                  Willowbrook               Burger Joint   

     2nd Most Common Venue  3rd Most Common Venue     4th Most Common Venue  \
2   Furniture / Home Store                   Café        Mexican Restaurant   
4        Mobile Phone Shop            Pizza Place        Mexican Restaurant   
8       Chinese Restaurant                 Bakery  Mediterranean Restaurant   
12            Intersection            Coffee Shop        Italian Restaurant   
15                     Bar     Italian Restaurant              Burger Joint   
21            Burger Joint  Vietnamese Restaurant        Mexican Restaurant   
22      Mexican Restaurant          Deli / Bodega              Burger Joint   
25             Coffee Shop                   Park        Mexican Restaurant   
27    Fast Food Restaurant            Pizza Place               Coffee Shop   
30              Restaurant            Coffee Shop       American Restaurant   
34     Fried Chicken Joint   Fast Food Restaurant            Sandwich Place   
35          Clothing Store       Department Store              Burger Joint   
36      Mexican Restaurant     Italian Restaurant                      Café   
38      Mexican Restaurant            Coffee Shop               Pizza Place   
43          Airport Lounge        Airport Service            Sandwich Place   
45             Pizza Place                   Park               Coffee Shop   
49             Gas Station         Sandwich Place                     Hotel   
53            Burger Joint            Coffee Shop            Sandwich Place   
54             Coffee Shop    American Restaurant            Clothing Store   
55           Grocery Store     Mexican Restaurant               Coffee Shop   
56      Mexican Restaurant         

## Cluster 3

In [95]:
Houston_merged.loc[Houston_merged['Cluster Labels'] == 3, Houston_merged.columns[[1] + list(range(5, Houston_merged.shape[1]))]]


Neighborhood 1st Most Common Venue  \
3                          Alief  Fast Food Restaurant   
7                     Brays Oaks  Fast Food Restaurant   
11             Central Southwest   Fried Chicken Joint   
16                  East Houston  Fast Food Restaurant   
17  East Little York / Homestead        Discount Store   
18          Eastex - Jensen Area  Fast Food Restaurant   
23               Fondren Gardens  Fast Food Restaurant   
28            Greater Fifth Ward  Fast Food Restaurant   
32                Greater Inwood  Fast Food Restaurant   
33            Greater Third Ward  Fast Food Restaurant   
37                       Gulfton  Fast Food Restaurant   
40                    Hunterwood  Fast Food Restaurant   
44                 Kingwood Area        Discount Store   
50                 Magnolia Park  Fast Food Restaurant   
52           Medical Center Area        Discount Store   
62           Northside/Northline  Fast Food Restaurant   
68                     Settegast   Fried Chicken Joint   
73                    South Park           Gas Station   
78                     Sunnyside   Fried Chicken Joint   
79     Trinity / Houston Gardens             BBQ Joint   
83                      Westbury         Grocery Store   

     2nd Most Common Venue 3rd Most Common Venue   4th Most Common Venue  \
3              Pizza Place         Grocery Store          Discount Store   
7            Grocery Store        Discount Store             Pizza Place   
11             Gas Station  Fast Food Restaurant          Discount Store   
16          Discount Store   Fried Chicken Joint          Cosmetics Shop   
17                    Food     Convenience Store             Gas Station   
18          Discount Store           Gas Station             Pizza Place   
23          Discount Store   Fried Chicken Joint       Mobile Phone Shop   
28      Mexican Restaurant                  Park            Intersection   
32                Pharmacy           Pizza Place          Discount Store   
33     Fried Chicken Joint           Gas Station             Pizza Place   
37          Discount Store    Mexican Restaurant  Furniture / Home Store   
40           Grocery Store        Breakfast Spot       Convenience Store   
44     Fried Chicken Joint  Fast Food Restaurant               Nightclub   
50     Fried Chicken Joint           Pizza Place          Sandwich Place   
52             Pizza Place    Mexican Restaurant           Grocery Store   
62  Furniture / Home Store        Sandwich Place          Discount Store   
68    Fast Food Restaurant        Discount Store                Bus Stop   
73     Fried Chicken Joint          Burger Joint    Fast Food Restaurant   
78          Discount Store  Fast Food Restaurant             Pizza Place   
79          Discount Store           Gas Station                Bus Stop   
83             Pizza Place                  Bank                    Park   

            5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
3               Mobile Phone Shop           Video Store        Cosmetics Shop   
7                            Bank   Fried Chicken Joint              Pharmacy   
11             Chinese Restaurant    Seafood Restaurant           Bus Station   
16               Storage Facility     Mobile Phone Shop         Grocery Store   
17                 Clothing Store                  Park                   Spa   
18            Fried Chicken Joint                  Bank         Event Service   
23                 Sandwich Place          Intersection                  Park   
28                       Pharmacy           Gas Station   American Restaurant   
32  Paper / Office Supplies Store       Automotive Shop        Sandwich Place   
33                   Burger Joint        Discount Store                Market   
37              Convenience Store            Taco Place                Bakery   
40                    Pizza Place        Sandwich Place              Pharmacy   
44               

## Cluster 4

In [96]:
Houston_merged.loc[Houston_merged['Cluster Labels'] == 4, Houston_merged.columns[[1] + list(range(5, Houston_merged.shape[1]))]]


Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
46     Langwood                  Park                  Lake   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
46           Auto Garage       Vacation Rental                 Beach   

   6th Most Common Venue          7th Most Common Venue 8th Most Common Venue  
46        Scenic Lookout  Paper / Office Supplies Store  Pakistani Restaurant

## Cluster 5

In [97]:
Houston_merged.loc[Houston_merged['Cluster Labels'] == 5, Houston_merged.columns[[1] + list(range(5, Houston_merged.shape[1]))]]


Neighborhood  1st Most Common Venue  \
5                           Braeburn         Discount Store   
6                    Braeswood Place     Mexican Restaurant   
9                         Carverdale            Gas Station   
10                 Central Northwest                   Park   
13        Clinton Park Tri-Community            Post Office   
14      Denver Harbor / Port Houston     Mexican Restaurant   
19                    Edgebrook Area   Fast Food Restaurant   
20         El Dorado / Oates Prairie         Ice Cream Shop   
26   Golfcrest / Bellfort / Reveille            Pizza Place   
29               Greater Greenspoint   Fast Food Restaurant   
31                Greater Hobby Area     Mexican Restaurant   
41                Iah / Airport Area           Intersection   
42              Independence Heights      Mobile Phone Shop   
47                Lawndale / Wayside                  Hotel   
48          Lazy Brook / Timbergrove     Mexican Restaurant   
51           Meadowbrook / Allendale     Mexican Restaurant   
61                 Northside Village     Mexican Restaurant   
63                 Ost / South Union     Mexican Restaurant   
64                        Park Place                   Park   
65                        Pecan Park     Mexican Restaurant   
66                Pleasantville Area            Gas Station   
67                       Second Ward     Mexican Restaurant   
69                        Sharpstown    Fried Chicken Joint   
71            South Belt / Ellington  Vietnamese Restaurant   
72                        South Main   Fast Food Restaurant   
74             Spring Branch Central     Mexican Restaurant   
75                Spring Branch East     Mexican Restaurant   
76               Spring Branch North            Pizza Place   
82                        Westbranch            Gas Station   
85                          Westwood   Fast Food Restaurant   
86  Willow Meadows / Willowbend Area   Fast Food Restaurant   

   2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
5               Pharmacy        Clothing Store    Chinese Restaurant   
6         Sandwich Place            Donut Shop          Burger Joint   
9              BBQ Joint                 Hotel        Breakfast Spot   
10           Gas Station        Discount Store           Pizza Place   
13                Lawyer         Boat or Ferry           Gas Station   
14           Gas Station  Fast Food Restaurant        Sandwich Place   
19    Mexican Restaurant           Pizza Place        Sandwich Place   
20    Mexican Restaurant          Intersection   Rental Car Location   
26    Mexican Restaurant        Breakfast Spot  Fast Food Restaurant   
29    Mexican Restaurant        Sandwich Place           Pizza Place   
31        Discount Store        Ice Cream Shop           Gas Station   
41        Sandwich Place           Gas Station      Business Service   
42        Discount Store    Mexican Restaurant           Pizza Place   
47  Fast Food Restaurant                  Bank        Sandwich Place   
48        Discount Store  Fast Food Restaurant            Taco Place   
51    Chinese Restaurant  Fast Food Restaurant    Seafood Restaurant   
61  Fast Food Restaurant        Discount Store     Convenience Store   
63        Discount Store           Video Store        Sandwich Place   
64    Mexican Restaurant           Gas Station        Discount Store   
65           Pizza Place        Discount Store        Breakfast Spot   
66    Mexican Restaurant   Fried Chicken Joint                  Bank   
67              Dive Bar  Fast Food Restaurant           Gas Station   
69           Pizza Place              Pharmacy  Fast Food Restaurant   
71           Pizza Place    Mexican Restaurant  Fast Food Restaurant   
72    Mexican Restaurant            Sports Bar   Fried Chicken Joint   
74        Sandwich Place  Gym / Fitness Center              Pharmacy   
75           Pizza Place                  Bank        Sandwich 

## Cluster 6

In [98]:
Houston_merged.loc[Houston_merged['Cluster Labels'] == 6, Houston_merged.columns[[1] + list(range(5, Houston_merged.shape[1]))]]


Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
39  Hidden Valley         Boat or Ferry                  Park   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
39       Marine Terminal  Fast Food Restaurant    Mexican Restaurant   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  
39  Other Great Outdoors  Pakistani Restaurant       Paintball Field

## Cluster 7

In [99]:
Houston_merged.loc[Houston_merged['Cluster Labels'] == 7, Houston_merged.columns[[1] + list(range(5, Houston_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
58                   Museum Park           IT Services        Discount Store   
70  South Acres / Crestmont Park         Grocery Store        Discount Store   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
58           Gas Station        Clothing Store         Grocery Store   
70     Convenience Store                  Park    Seafood Restaurant   

   6th Most Common Venue          7th Most Common Venue 8th Most Common Venue  
58     Other Repair Shop  Paper / Office Supplies Store  Pakistani Restaurant  
70             Pet Store                    Gas Station      Business Service

# Cluster Neighborhoods
#### Drop clusters with only one neighborhood (e.g. Clusters 6)

In [25]:
Houston_grouped_01=Houston_grouped.drop([0, 1, 20, 46, 70])
Houston_grouped_01.iloc[1]

Neighborhood Name                               Alief
ATM                                                 0
Accessories Store                                   0
Advertising Agency                                  0
Afghan Restaurant                                   0
African Restaurant                                  0
Airport                                             0
Airport Lounge                                      0
Airport Service                                     0
Airport Terminal                                    0
American Restaurant                                 0
Aquarium                                            0
Arcade                                              0
Argentinian Restaurant                              0
Art Gallery                                         0
Art Museum                                          0
Arts & Crafts Store                                 0
Asian Restaurant                            0.0217391
Athletics & Sports          

In [26]:
#### Run k-means to cluster the neighborhood into 7 clusters.

# set number of clusters
kclusters = 7

Houston_grouped_01_clustering = Houston_grouped_01.drop('Neighborhood Name', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0, max_iter=1000, tol=0.01).fit(Houston_grouped_01_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_

array([2, 5, 2, 5, 5, 5, 2, 5, 5, 6, 5, 0, 5, 2, 0, 3, 0, 5, 2, 2, 5, 3,
       2, 5, 5, 5, 5, 2, 1, 5, 0, 5, 2, 2, 5, 2, 3, 5, 0, 5, 2, 6, 5, 5,
       5, 2, 5, 1, 3, 2, 2, 2, 2, 2, 4, 2, 2, 5, 5, 1, 5, 5, 1, 1, 6, 5,
       5, 5, 6, 1, 5, 5, 2, 6, 6, 2, 2, 5, 5, 2, 5, 5, 2], dtype=int32)

In [27]:
#### Create a new dataframe and display the top 10 venues for each neighborhood.
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood Name']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood Name'] = Houston_grouped_01['Neighborhood Name']

for ind in np.arange(Houston_grouped_01.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(Houston_grouped_01.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.shape

(83, 11)

In [28]:
#### Create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.

# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

Houston_merged_01 = Demographic[['Location', 'Neighborhood', 'Latitude', 'Longitude']].drop([0, 1, 20, 46, 70])

# merge Houston_grouped with toronto_data to add latitude/longitude for each neighborhood
Houston_merged_01 = Houston_merged_01.join(neighborhoods_venues_sorted.set_index('Neighborhood Name'), on='Neighborhood')

Houston_merged_01.shape # check the last columns!

(83, 15)

In [29]:
# create map
map_clusters_01 = folium.Map(location=[29.8, -95.3676974], zoom_start=10)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(Houston_merged_01['Latitude'], Houston_merged_01['Longitude'], Houston_merged_01['Neighborhood'], Houston_merged_01['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=3,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters_01)
       
map_clusters_01

## Analyze each cluster

### Cluster 0
This cluster has various types of restaurants and some coffee shop. 

In [265]:
Houston_merged_01.loc[Houston_merged_01['Cluster Labels'] == 0, Houston_merged_01.columns[[1] + list(range(5, Houston_merged_01.shape[1]))]]


Neighborhood   1st Most Common Venue  \
2                  Afton Oaks / River Oaks Area  Furniture / Home Store   
15                                     Downtown                   Hotel   
25                                  Fourth Ward            Burger Joint   
30                              Greater Heights      Mexican Restaurant   
35                  Greenway / Upper Kirby Area                   Hotel   
36             Gulfgate Riverview / Pine Valley                  Bakery   
43                             Kashmere Gardens             Coffee Shop   
53                                     Memorial             Zoo Exhibit   
54                               Meyerland Area      Mexican Restaurant   
57                                     Minnetex   Vietnamese Restaurant   
59                          Neartown - Montrose             Zoo Exhibit   
60                                   Northshore             Coffee Shop   
77                           Spring Branch West       Korean Restaurant   
80                             University Place             Coffee Shop   
81  Washington Avenue Coalition / Memorial Park                    Park   
87                                  Willowbrook            Burger Joint   

      2nd Most Common Venue     3rd Most Common Venue  \
2   New American Restaurant        Mexican Restaurant   
15                      Bar        Italian Restaurant   
25              Coffee Shop               Pizza Place   
30                Juice Bar                 Gift Shop   
35             Burger Joint            Clothing Store   
36       Seafood Restaurant        Mexican Restaurant   
43         Airport Terminal            Sandwich Place   
53             Burger Joint               Coffee Shop   
54      American Restaurant            Clothing Store   
57                      Bar               Coffee Shop   
59              Coffee Shop                       Bar   
60       Italian Restaurant              Cocktail Bar   
77           Cosmetics Shop  Mediterranean Restaurant   
80           Ice Cream Shop        Italian Restaurant   
81                    Trail                       Bar   
87         Department Store               Coffee Shop   

      4th Most Common Venue 5th Most Common Venue    6th Most Common Venue  \
2        Seafood Restaurant      Sushi Restaurant                     Café   
15             Burger Joint           Coffee Shop                   Lounge   
25                     Park               Theater       Mexican Restaurant   
30       Italian Restaurant                  Café  New American Restaurant   
35         Department Store   American Restaurant           Cosmetics Shop   
36             Burger Joint    Italian Restaurant              Coffee Shop   
43           Airport Lounge  Fast Food Restaurant                  Airport   
53     Fast Food Restaurant            Restaurant      American Restaurant   
54           Breakfast Spot           Coffee Shop            Shopping Mall   
57       Mexican Restaurant        Breakfast Spot              Pizza Place   
59               Art Museum        Science Museum                    Trail   
60  New American Restaurant                   Bar                      Gym   
77           Clothing Store          Burger Joint               Steakhouse   
80      American Restaurant                   Bar             Burger Joint   
81      American Restaurant            Restaurant           Baseball Field   
87           Clothing Store    Mexican Restaurant   Furniture / Home Store   

   7th Most Common Venue            8th Most Common Venue  \
2           Burger Joint                   Cosmetics Shop   
15          Cocktail Bar                      Music Venue   
25   American Restaurant  Southern / Soul Food Restaurant   
30                  Park                       Taco Place   
35    Mexican Restaurant                       Steakhouse   
36    Chinese Restaurant                 Sushi Restaurant   
43     Electronics Store           

### Cluster 1
This cluster although mainly has restaurant and food services, the venues categories are quite diverse. Cluster 1 contains too much data, and here only show part of it; therefore, further analysis is needed. Cluster 1 was extracted and clustered using K-means with 7 cluster centroids.

In [266]:
Houston_merged_01.loc[Houston_merged_01['Cluster Labels'] == 1, Houston_merged_01.columns[[1] + list(range(5, Houston_merged_01.shape[1]))]]


Neighborhood      1st Most Common Venue  \
4                     Astrodome Area          Mobile Phone Shop   
5                           Braeburn             Discount Store   
6                    Braeswood Place       Fast Food Restaurant   
8                   Briarforest Area             Sandwich Place   
9                         Carverdale                Gas Station   
10                 Central Northwest                       Park   
12                        Clear Lake                Pizza Place   
21              Eldridge / West Oaks             Sandwich Place   
22    Fairbanks / Northwest Crossing         Seafood Restaurant   
26   Golfcrest / Bellfort / Reveille         Mexican Restaurant   
27                  Greater Eastwood       Fast Food Restaurant   
29               Greater Greenspoint       Fast Food Restaurant   
34                    Greater Uptown       Fast Food Restaurant   
38           Harrisburg / Manchester       Fast Food Restaurant   
42              Independence Heights          Mobile Phone Shop   
45                      Lake Houston       Fast Food Restaurant   
47                Lawndale / Wayside                      Hotel   
49                         Macgregor         Mexican Restaurant   
55                          Mid West           Department Store   
56                           Midtown  Middle Eastern Restaurant   
63                 Ost / South Union         Mexican Restaurant   
64                        Park Place                Gas Station   
65                        Pecan Park         Mexican Restaurant   
66                Pleasantville Area         Mexican Restaurant   
67                       Second Ward         Mexican Restaurant   
69                        Sharpstown        Fried Chicken Joint   
71            South Belt / Ellington       Fast Food Restaurant   
72                        South Main         Mexican Restaurant   
74             Spring Branch Central         Mexican Restaurant   
75                Spring Branch East       Fast Food Restaurant   
76               Spring Branch North         Mexican Restaurant   
82                        Westbranch                Gas Station   
84                         Westchase             Sandwich Place   
85                          Westwood       Fast Food Restaurant   
86  Willow Meadows / Willowbend Area       Fast Food Restaurant   

    2nd Most Common Venue   3rd Most Common Venue 4th Most Common Venue  \
4          Sandwich Place      Mexican Restaurant           Pizza Place   
5                Pharmacy          Cosmetics Shop        Sandwich Place   
6      Mexican Restaurant      Chinese Restaurant           Pizza Place   
8           Grocery Store      Chinese Restaurant    Mexican Restaurant   
9               BBQ Joint                   Hotel        Sandwich Place   
10            Gas Station      Mexican Restaurant           Pizza Place   
12                   Bank             Coffee Shop    Italian Restaurant   
21            Coffee Shop      Mexican Restaurant          Burger Joint   
22     Mexican Restaurant    Fast Food Restaurant                Bakery   
26            Pizza Place                   Diner  Fast Food Restaurant   
27            Coffee Shop                     Bar            Food Truck   
29            Pizza Place      Mexican Restaurant        Discount Store   
34            Coffee Shop          Sandwich Place           Pizza Place   
38      Indian Restaurant             Coffee Shop    Mexican Restaurant   
42         Discount Store             Gas Station   Fried Chicken Joint   
45            Pizza Place                    Park           Coffee Shop   
47   Fast Food Restaurant             Pizza Place        Sandwich Place   
49            Gas Station          Sandwich Place                 Hotel   
55            Pizza Place  Furniture / Home Store  Fast Food Restaurant   
56     Mexican Restaurant              Food Truck             BBQ Joint   
63         Discount Store           

### Cluster 2
This cluster has unique venue categories distribution, which has park, zoo and stores.

In [267]:
Houston_merged_01.loc[Houston_merged_01['Cluster Labels'] == 2, Houston_merged_01.columns[[1] + list(range(5, Houston_merged_01.shape[1]))]]


Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
58  Museum Park        Clothing Store                  Park   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
58        Discount Store           Gas Station           Zoo Exhibit   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
58        Duty-free Shop     Electronics Store   Empanada Restaurant   

   9th Most Common Venue 10th Most Common Venue  
58  Ethiopian Restaurant          Event Service

### Cluster 3
This cluster mainly has stores and fast food restaurant.

In [268]:
Houston_merged_01.loc[Houston_merged_01['Cluster Labels'] == 3, Houston_merged_01.columns[[1] + list(range(5, Houston_merged_01.shape[1]))]]


Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
16                  East Houston  Fast Food Restaurant    Seafood Restaurant   
17  East Little York / Homestead        Discount Store                  Food   
18          Eastex - Jensen Area        Discount Store  Fast Food Restaurant   
44                 Kingwood Area        Discount Store  Fast Food Restaurant   
78                     Sunnyside        Discount Store   Fried Chicken Joint   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
16        Discount Store   Fried Chicken Joint         Grocery Store   
17        Clothing Store               Brewery   Fried Chicken Joint   
18           Pizza Place           Gas Station            Food Truck   
44   Fried Chicken Joint                 Motel      Department Store   
78           Pizza Place  Fast Food Restaurant     Convenience Store   

   6th Most Common Venue            7th Most Common Venue  \
16     Mobile Phone Shop                   Waste Facility   
17                   Spa                      Gas Station   
18   Arts & Crafts Store                          Brewery   
44        General Travel                    Auto Workshop   
78    Chinese Restaurant  Southern / Soul Food Restaurant   

         8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
16              Sandwich Place            Donut Shop       Video Game Store  
17                        Park     Convenience Store            Pizza Place  
18  Construction & Landscaping           Supermarket    Fried Chicken Joint  
44          Chinese Restaurant         Grocery Store         Sandwich Place  
78           Electronics Store            Shoe Store                   Bank

### Cluster 4
This cluster mainly has fast food restaurant, fried chicken and donuts place.

In [269]:
Houston_merged_01.loc[Houston_merged_01['Cluster Labels'] == 4, Houston_merged_01.columns[[1] + list(range(5, Houston_merged_01.shape[1]))]]


Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
11           Central Southwest   Fried Chicken Joint  Fast Food Restaurant   
13  Clinton Park Tri-Community         Boat or Ferry  Fast Food Restaurant   
33          Greater Third Ward   Fried Chicken Joint  Fast Food Restaurant   
41          Iah / Airport Area  Fast Food Restaurant            Donut Shop   
68                   Settegast              Bus Stop  Fast Food Restaurant   
73                  South Park           Gas Station          Burger Joint   
79   Trinity / Houston Gardens        Discount Store     Convenience Store   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
11           Gas Station             Nightclub          Home Service   
13            Donut Shop        Discount Store        Sandwich Place   
33           Gas Station           Pizza Place         Grocery Store   
41  Gym / Fitness Center          Home Service   Rental Car Location   
68        Discount Store   Fried Chicken Joint     Convenience Store   
73  Fast Food Restaurant   Fried Chicken Joint        Discount Store   
79           Gas Station   Fried Chicken Joint             BBQ Joint   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
11     Convenience Store        Discount Store          Intersection   
13                Lawyer           Gas Station             BBQ Joint   
33          Burger Joint                Market            Donut Shop   
41   Fried Chicken Joint          Intersection           Gas Station   
68          Burger Joint                  Park  Gym / Fitness Center   
73    Salon / Barbershop        Cosmetics Shop        Baseball Field   
79  Fast Food Restaurant              Pharmacy    Seafood Restaurant   

   9th Most Common Venue      10th Most Common Venue  
11        Shop & Service                 Video Store  
13   Filipino Restaurant  Financial or Legal Service  
33        Sandwich Place                   BBQ Joint  
41        Sandwich Place                 Dry Cleaner  
68        Sandwich Place                 Video Store  
73           Pizza Place                    Pharmacy  
79          Burger Joint              Sandwich Place

### Cluster 5
This cluster has unique venue categories distribution, which has food truck, BBQ, park, and stores.

In [270]:
Houston_merged_01.loc[Houston_merged_01['Cluster Labels'] == 5, Houston_merged_01.columns[[1] + list(range(5, Houston_merged_01.shape[1]))]]


Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
24  Fort Bend / Houston            Food Truck             BBQ Joint   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
24     Convenience Store        Discount Store                  Park   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
24         Moving Target             Gastropub                 Hotel   

   9th Most Common Venue 10th Most Common Venue  
24  Himalayan Restaurant          Event Service

### Cluster 6
This cluster mainly has fast food restaurant, Mexican restaurant, pizza place and a few stores and parks.

In [271]:
Houston_merged_01.loc[Houston_merged_01['Cluster Labels'] == 6, Houston_merged_01.columns[[1] + list(range(5, Houston_merged_01.shape[1]))]]


Neighborhood 1st Most Common Venue  \
3                          Alief  Fast Food Restaurant   
7                     Brays Oaks        Discount Store   
14  Denver Harbor / Port Houston           Gas Station   
19                Edgebrook Area  Fast Food Restaurant   
23               Fondren Gardens  Fast Food Restaurant   
28            Greater Fifth Ward    Mexican Restaurant   
31            Greater Hobby Area    Mexican Restaurant   
32                Greater Inwood  Fast Food Restaurant   
37                       Gulfton  Fast Food Restaurant   
39                 Hidden Valley                  Park   
40                    Hunterwood  Fast Food Restaurant   
48      Lazy Brook / Timbergrove    Mexican Restaurant   
50                 Magnolia Park  Fast Food Restaurant   
51       Meadowbrook / Allendale    Mexican Restaurant   
52           Medical Center Area        Discount Store   
61             Northside Village    Mexican Restaurant   
62           Northside/Northline  Fast Food Restaurant   
83                      Westbury           Pizza Place   

     2nd Most Common Venue 3rd Most Common Venue  4th Most Common Venue  \
3              Pizza Place        Discount Store  Vietnamese Restaurant   
7            Grocery Store  Fast Food Restaurant            Pizza Place   
14      Mexican Restaurant  Fast Food Restaurant            Pizza Place   
19      Mexican Restaurant           Pizza Place         Sandwich Place   
23             Gas Station        Discount Store                   Park   
28    Fast Food Restaurant                  Park           Intersection   
31    Fast Food Restaurant            Food Truck           Burger Joint   
32             Pizza Place              Pharmacy            Video Store   
37       Convenience Store    Mexican Restaurant         Discount Store   
39         Harbor / Marina         Boat or Ferry           Home Service   
40  Furniture / Home Store         Grocery Store            Pizza Place   
48    Fast Food Restaurant           Pizza Place     Seafood Restaurant   
50     Fried Chicken Joint           Pizza Place            Coffee Shop   
51    Fast Food Restaurant         Grocery Store    Fried Chicken Joint   
52             Pizza Place          Liquor Store   Fast Food Restaurant   
61          Discount Store  Fast Food Restaurant            Pizza Place   
62          Discount Store    Mexican Restaurant    Fried Chicken Joint   
83                    Bank                  Park         Baseball Field   

     5th Most Common Venue 6th Most Common Venue   7th Most Common Venue  \
3            Grocery Store           Gas Station              Taco Place   
7                     Bank        Sandwich Place                Pharmacy   
14          Sandwich Place                  Bank                Pharmacy   
19      Seafood Restaurant                  Bank          Discount Store   
23          Sandwich Place   Fried Chicken Joint  Thrift / Vintage Store   
28          Discount Store           Gas Station                Pharmacy   
31             Gas Station        Discount Store        Airport Terminal   
32          Discount Store                 Trail           Grocery Store   
37  Furniture / Home Store            Taco Place          Hardware Store   
39          Discount Store           Pizza Place      Mexican Restaurant   
40                Pharmacy   Fried Chicken Joint                   Diner   
48          Discount Store            Taco Place                    Park   
50               BBQ Joint             Nightclub          Sandwich Place   
51      Seafood Restaurant           Snack Place       Convenience Store   
52           Grocery Store           Gas Station              Food Truck   
61             Gas Station        Sandwich Place     Fried Chicken Joint   
62             Gas Station        Sandwich Place      Seafood Restaurant   
83           Grocery Store            Hobby Shop    Fast Food Restaurant   

   8th Most Common Venue 9th Most Common Venue

### Reprocess Cluster 1 because it contains too much data

In [30]:
cluster1 = Houston_merged_01.loc[Houston_merged_01['Cluster Labels'] == 1]
len(cluster1)
cluster1.index


Int64Index([31, 51, 63, 66, 67, 74], dtype='int64')

In [31]:
Houston_grouped_02=Houston_grouped.iloc[[4, 5, 6, 8, 9, 10, 12, 21, 22, 26, 27, 29, 34, 38, 42, 45, 47,49, 55, 56, 63, 64, 65, 66, 67, 69, 71, 72, 74, 75, 76, 82, 84, 85,86], :]
Houston_grouped_02.iloc[1]


Neighborhood Name                           Braeburn
ATM                                                0
Accessories Store                                  0
Advertising Agency                                 0
Afghan Restaurant                                  0
African Restaurant                                 0
Airport                                            0
Airport Lounge                                     0
Airport Service                                    0
Airport Terminal                                   0
American Restaurant                           0.0125
Aquarium                                           0
Arcade                                             0
Argentinian Restaurant                             0
Art Gallery                                        0
Art Museum                                         0
Arts & Crafts Store                                0
Asian Restaurant                              0.0125
Athletics & Sports                            

In [32]:
Houston_grouped_02.shape

(35, 335)

In [34]:
#### Run k-means to cluster the neighborhood into 7 clusters.

# set number of clusters
kclusters = 7

Houston_grouped_02_clustering = Houston_grouped_02.drop('Neighborhood Name', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(Houston_grouped_02_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_

array([2, 0, 5, 2, 3, 0, 6, 2, 2, 5, 2, 5, 2, 2, 5, 5, 3, 1, 2, 2, 1, 0,
       5, 4, 1, 0, 5, 5, 1, 5, 5, 3, 2, 5, 5], dtype=int32)

In [35]:
#### Create a new dataframe and display the top 10 venues for each neighborhood.
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood Name']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood Name'] = Houston_grouped_02['Neighborhood Name']

for ind in np.arange(Houston_grouped_02.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(Houston_grouped_02.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.shape

(35, 11)

In [36]:
#### Create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.

# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

Houston_merged_02 = Demographic[['Location', 'Neighborhood', 'Latitude', 'Longitude']].iloc[[4, 5, 6, 8, 9, 10, 12, 21, 22, 26, 27, 29, 34, 38, 42, 45, 47,49, 55, 56, 63, 64, 65, 66, 67, 69, 71, 72, 74, 75, 76, 82, 84, 85,86], :]

# merge Houston_grouped with toronto_data to add latitude/longitude for each neighborhood
Houston_merged_02 = Houston_merged_02.join(neighborhoods_venues_sorted.set_index('Neighborhood Name'), on='Neighborhood')

Houston_merged_02.shape # check the last columns!

(35, 15)

In [41]:
# create map
map_clusters_02 = folium.Map(location=[29.8, -95.3676974], zoom_start=10)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(Houston_merged_02['Latitude'], Houston_merged_02['Longitude'], Houston_merged_02['Neighborhood'], Houston_merged_02['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=3,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters_02)
       
map_clusters_02

### Cluster 1-0
This cluster mainly has gas station and Mexican restaurant.

In [38]:
Houston_merged_02.loc[Houston_merged_02['Cluster Labels'] == 0, Houston_merged_02.columns[[1] + list(range(5, Houston_merged_02.shape[1]))]]


Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
5            Braeburn        Discount Store              Pharmacy   
10  Central Northwest                  Park           Gas Station   
64         Park Place           Gas Station        Discount Store   
69         Sharpstown   Fried Chicken Joint           Pizza Place   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
5         Cosmetics Shop        Sandwich Place                  Bank   
10    Mexican Restaurant           Pizza Place                   Spa   
64    Mexican Restaurant           Golf Course          Home Service   
69        Sandwich Place              Pharmacy  Fast Food Restaurant   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
5                    Bar   Rental Car Location           Pizza Place   
10                 Trail      Business Service                   Bar   
64         Moving Target        Baseball Field           Pizza Place   
69            Restaurant     Convenience Store  Gym / Fitness Center   

   9th Most Common Venue 10th Most Common Venue  
5     Chinese Restaurant         Clothing Store  
10     Convenience Store                   Bank  
64     Mobile Phone Shop         Breakfast Spot  
69           College Gym      Korean Restaurant

### Cluster 1-1
This cluster mainly has Mexican restaurant, gas station and hotel.

In [349]:
Houston_merged_02.loc[Houston_merged_02['Cluster Labels'] == 1, Houston_merged_02.columns[[1] + list(range(5, Houston_merged_02.shape[1]))]]


Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
49              Macgregor    Mexican Restaurant           Gas Station   
63      Ost / South Union    Mexican Restaurant        Discount Store   
67            Second Ward    Mexican Restaurant  Fast Food Restaurant   
74  Spring Branch Central    Mexican Restaurant              Pharmacy   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
49        Sandwich Place                 Hotel    Italian Restaurant   
63                 Hotel   Fried Chicken Joint                  Park   
67                  Park           Gas Station         Grocery Store   
74         Grocery Store        Sandwich Place          Burger Joint   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
49                  Park              Wine Bar           Video Store   
63         Grocery Store           Gas Station           Video Store   
67           Snack Place                   Bar           Video Store   
74  Gym / Fitness Center        Discount Store            Taco Place   

   9th Most Common Venue 10th Most Common Venue  
49          Burger Joint         Baseball Field  
63        Sandwich Place             Food Truck  
67            Food Truck              BBQ Joint  
74           Video Store  Vietnamese Restaurant

### Cluster 1-2
This cluster mainly has fast food restaurant, sandwich place and coffee shop.

In [350]:
Houston_merged_02.loc[Houston_merged_02['Cluster Labels'] == 2, Houston_merged_02.columns[[1] + list(range(5, Houston_merged_02.shape[1]))]]


Neighborhood      1st Most Common Venue  \
4                   Astrodome Area          Mobile Phone Shop   
8                 Briarforest Area             Sandwich Place   
21            Eldridge / West Oaks             Sandwich Place   
22  Fairbanks / Northwest Crossing         Seafood Restaurant   
27                Greater Eastwood       Fast Food Restaurant   
34                  Greater Uptown       Fast Food Restaurant   
38         Harrisburg / Manchester       Fast Food Restaurant   
55                        Mid West           Department Store   
56                         Midtown  Middle Eastern Restaurant   
84                       Westchase             Sandwich Place   

   2nd Most Common Venue   3rd Most Common Venue 4th Most Common Venue  \
4         Sandwich Place      Mexican Restaurant           Pizza Place   
8          Grocery Store      Chinese Restaurant    Mexican Restaurant   
21           Coffee Shop      Mexican Restaurant          Burger Joint   
22    Mexican Restaurant    Fast Food Restaurant                Bakery   
27           Coffee Shop                     Bar            Food Truck   
34           Coffee Shop          Sandwich Place           Pizza Place   
38     Indian Restaurant             Coffee Shop    Mexican Restaurant   
55           Pizza Place  Furniture / Home Store  Fast Food Restaurant   
56    Mexican Restaurant              Food Truck             BBQ Joint   
84           Coffee Shop           Grocery Store                 Hotel   

   5th Most Common Venue 6th Most Common Venue  7th Most Common Venue  \
4             Sports Bar             BBQ Joint            Coffee Shop   
8               Pharmacy           Pizza Place            Coffee Shop   
21  Fast Food Restaurant     French Restaurant  Vietnamese Restaurant   
22    Miscellaneous Shop             BBQ Joint      Mobile Phone Shop   
27           Pizza Place        Sandwich Place             Taco Place   
34                   Bar            Bagel Shop                 Bakery   
38          Burger Joint   Fried Chicken Joint            Pizza Place   
55        Clothing Store           Coffee Shop     Mexican Restaurant   
56      Sushi Restaurant   Japanese Restaurant        Thai Restaurant   
84              Pharmacy                Bakery         Breakfast Spot   

    8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
4        Football Stadium                   Bar               Pharmacy  
8                  Bakery                 Hotel           Burger Joint  
21                 Bakery                  Bank        Thai Restaurant  
22  Vietnamese Restaurant          Burger Joint         Cosmetics Shop  
27            Gas Station    Mexican Restaurant         Discount Store  
34    Fried Chicken Joint            Food Truck          Smoothie Shop  
38             Taco Place         Grocery Store             Restaurant  
55           Burger Joint         Grocery Store            Gas Station  
56         Cosmetics Shop            Donut Shop    Sporting Goods Shop  
84     Seafood Restaurant          Burger Joint     Mexican Restaurant

### Cluster 1-3
This cluster mainly has gas station, hotel and BBQ.

In [351]:
Houston_merged_02.loc[Houston_merged_02['Cluster Labels'] == 3, Houston_merged_02.columns[[1] + list(range(5, Houston_merged_02.shape[1]))]]


Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
9           Carverdale           Gas Station             BBQ Joint   
47  Lawndale / Wayside                 Hotel  Fast Food Restaurant   
82          Westbranch           Gas Station                 Hotel   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
9                  Hotel        Sandwich Place          Burger Joint   
47           Pizza Place        Sandwich Place    Mexican Restaurant   
82                  Café             BBQ Joint          Burger Joint   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
9      Convenience Store            Taco Place                  Bank   
47           Gas Station                  Bank   Rental Car Location   
82  Fast Food Restaurant            Taco Place           Video Store   

   9th Most Common Venue  10th Most Common Venue  
9                   Café  Furniture / Home Store  
47            Donut Shop           Grocery Store  
82   Fried Chicken Joint              Donut Shop

### Cluster 1-4
This cluster has unique venue categories distribution, which mainly is Mexican restaurant, sandwich place and gas station.

In [352]:
Houston_merged_02.loc[Houston_merged_02['Cluster Labels'] == 4, Houston_merged_02.columns[[1] + list(range(5, Houston_merged_02.shape[1]))]]


Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
66  Pleasantville Area    Mexican Restaurant        Sandwich Place   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
66           Gas Station        Rental Service    Athletics & Sports   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
66     Electronics Store          Burger Joint                  Bank   

   9th Most Common Venue 10th Most Common Venue  
66   Fried Chicken Joint           Home Service

### Cluster 1-5
This cluster mainly has fast food restaurant, Mexican restaurant and pizza place.

In [353]:
Houston_merged_02.loc[Houston_merged_02['Cluster Labels'] == 5, Houston_merged_02.columns[[1] + list(range(5, Houston_merged_02.shape[1]))]]


Neighborhood 1st Most Common Venue  \
6                    Braeswood Place  Fast Food Restaurant   
26   Golfcrest / Bellfort / Reveille    Mexican Restaurant   
29               Greater Greenspoint  Fast Food Restaurant   
42              Independence Heights     Mobile Phone Shop   
45                      Lake Houston  Fast Food Restaurant   
65                        Pecan Park    Mexican Restaurant   
71            South Belt / Ellington  Fast Food Restaurant   
72                        South Main    Mexican Restaurant   
75                Spring Branch East  Fast Food Restaurant   
76               Spring Branch North    Mexican Restaurant   
85                          Westwood  Fast Food Restaurant   
86  Willow Meadows / Willowbend Area  Fast Food Restaurant   

    2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
6      Mexican Restaurant    Chinese Restaurant           Pizza Place   
26            Pizza Place                 Diner  Fast Food Restaurant   
29            Pizza Place    Mexican Restaurant        Discount Store   
42         Discount Store           Gas Station   Fried Chicken Joint   
45            Pizza Place                  Park           Coffee Shop   
65            Pizza Place        Discount Store   Fried Chicken Joint   
71  Vietnamese Restaurant           Pizza Place    Mexican Restaurant   
72   Fast Food Restaurant   Fried Chicken Joint            Sports Bar   
75     Mexican Restaurant                  Bank           Pizza Place   
76            Pizza Place  Fast Food Restaurant                  Park   
85      Mobile Phone Shop   Rental Car Location    Mexican Restaurant   
86     Mexican Restaurant   Fried Chicken Joint        Discount Store   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
6                 Bakery   Fried Chicken Joint            Donut Shop   
26          Burger Joint     Mobile Phone Shop        Breakfast Spot   
29        Sandwich Place                 Hotel            Shoe Store   
42    Mexican Restaurant           Pizza Place           Coffee Shop   
45   American Restaurant                  Bank                   Gym   
65           Gas Station     Mobile Phone Shop                 Diner   
71                  Bank         Grocery Store              Pharmacy   
72        Sandwich Place                   Bar             BBQ Joint   
75        Sandwich Place           Gas Station   Rental Car Location   
76           Video Store        Baseball Field                  Café   
85           Video Store         Grocery Store   Fried Chicken Joint   
86        Cosmetics Shop                Bakery           Coffee Shop   

   8th Most Common Venue            9th Most Common Venue  \
6               Pharmacy                      Coffee Shop   
26        Sandwich Place                         Pharmacy   
29                  Bank                     Burger Joint   
42                  Bank                        BBQ Joint   
45        Shipping Store               Chinese Restaurant   
65            Shoe Store                  Motorcycle Shop   
71           Video Store                     Burger Joint   
72      Football Stadium  Southern / Soul Food Restaurant   
75    Chinese Restaurant                   Breakfast Spot   
76        Sandwich Place            Vietnamese Restaurant   
85    African Restaurant                 Storage Facility   
86                  Bank                     Intersection   

       10th Most Common Venue  
6              Sandwich Place  
26                     Bakery  
29         Seafood Restaurant  
42       Fast Food Restaurant  
45              Grocery Store  
65             Sandwich Place  
71  Cajun / Creole Restaurant  
72                 Restaurant  
75      Vietnamese Restaurant  
76        Fried Chicken Joint  
85                        Bar  
86             Sandwich Place

### Cluster 1-6
This cluster has unique venue categories distribution, which mainly is pizza place, bank and coffee shop.

In [354]:
Houston_merged_02.loc[Houston_merged_02['Cluster Labels'] == 6, Houston_merged_02.columns[[1] + list(range(5, Houston_merged_02.shape[1]))]]


Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
12   Clear Lake           Pizza Place                  Bank   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
12           Coffee Shop    Italian Restaurant    Salon / Barbershop   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
12        Sandwich Place          Intersection                   Spa   

   9th Most Common Venue 10th Most Common Venue  
12           Gas Station           Liquor Store

# Discussion 

The ideal location to run a coffee shop would be the neighborhood that does not have too many coffee shops or similar substitute. The ideal location would also be the place with more people and higher income.
Based on the neighborhood clustering analysis, Cluster 0 already has a lot of restaurant as well as coffee shops and café so would not be considered at this point. Cluster 2 has a very unique venue distribution, which is a more service oriented neighborhood. Although this neighborhood is not popular with coffee shops, people may not spend their time here for coffee instead for certain destination only. Cluster 3 and 1-0 have restaurants and stores, which means people do spend their time having life in the neighborhoods; however, this cluster do not popular with coffee shop. Therefore, Cluster 3 may be a potential candidate to run a coffee shop. Cluster 4 has mainly fast food, fried chick and donuts and this food tend to be faster which may suggest that neighborhoods in Cluster 4 more likely to have something quick and therefore not the slow brewing coffee so Cluster 4 may not be an idea place. Cluster 5 and 1-4 has a very unique venue distribution, which does not have coffee shop and therefore can be a possible candidate. Cluster 6 and 1-5 has mainly fast food and pizza place, which may also suggest that people in these neighborhoods tend to have something fast and therefore not an ideal place for coffee shop. Cluster 1-1 and 1-3 are popular with hotel, which may indicate that people in this neighborhood are mostly traveler and therefore would not hang around the neighborhood so would not be an ideal place to run a coffee shop. Cluster 1-2 already has certain amount of coffee shops, which makes it less likely a place to run a coffee shop. Cluster 1-6 has a very unique venue distribution, which is popular with coffee shop and therefore is less likely an ideal place to run a coffee shop.

### Generate map

In [42]:
# create map of Houston City using latitude and longitude values
latitude=29.83
longitude = -95.2676974
map_houston_01 = folium.Map(location=[latitude, longitude], zoom_start=10)

# generate choropleth map 
houston_geo = r'houston_geo.json'
map_houston_01.choropleth(
    geo_data=houston_geo,
    data=Demographic,
    columns=['Neighborhood','Persons per Square Mile'],
    key_on='feature.properties.name',
    fill_color='YlOrRd', 
    fill_opacity=0.7, 
    line_opacity=0.2,
    legend_name='Persons per Square Mile'
)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(Houston_merged_01['Latitude'], Houston_merged_01['Longitude'], Houston_merged_01['Neighborhood'], Houston_merged_01['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=3,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_houston_01)
    

# display map
map_houston_01

In [43]:
# create map of Houston City using latitude and longitude values
latitude=29.83
longitude = -95.2676974
map_houston_01 = folium.Map(location=[latitude, longitude], zoom_start=10)

# generate choropleth map 
houston_geo = r'houston_geo.json'
map_houston_01.choropleth(
    geo_data=houston_geo,
    data=Demographic,
    columns=['Neighborhood','Median Household Income (USD)'],
    key_on='feature.properties.name',
    fill_color='YlOrRd', 
    fill_opacity=0.7, 
    line_opacity=0.2,
    legend_name='Median Household Income (USD)'
)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(Houston_merged_01['Latitude'], Houston_merged_01['Longitude'], Houston_merged_01['Neighborhood'], Houston_merged_01['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=3,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_houston_01)
    

# display map
map_houston_01

In [44]:
# create map of Houston City using latitude and longitude values
latitude=29.83
longitude = -95.2676974
map_houston_02 = folium.Map(location=[latitude, longitude], zoom_start=10)

# generate choropleth map 
houston_geo = r'houston_geo.json'
map_houston_02.choropleth(
    geo_data=houston_geo,
    data=Demographic,
    columns=['Neighborhood','Persons per Square Mile'],
    key_on='feature.properties.name',
    fill_color='YlOrRd', 
    fill_opacity=0.7, 
    line_opacity=0.2,
    legend_name='Persons per Square Mile'
)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(Houston_merged_02['Latitude'], Houston_merged_02['Longitude'], Houston_merged_02['Neighborhood'], Houston_merged_02['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=3,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_houston_02)
    

# display map
map_houston_02

In [45]:
# create map of Houston City using latitude and longitude values
latitude=29.83
longitude = -95.2676974
map_houston_02 = folium.Map(location=[latitude, longitude], zoom_start=10)

# generate choropleth map 
houston_geo = r'houston_geo.json'
map_houston_02.choropleth(
    geo_data=houston_geo,
    data=Demographic,
    columns=['Neighborhood','Median Household Income (USD)'],
    key_on='feature.properties.name',
    fill_color='YlOrRd', 
    fill_opacity=0.7, 
    line_opacity=0.2,
    legend_name='Median Household Income (USD)'
)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(Houston_merged_02['Latitude'], Houston_merged_02['Longitude'], Houston_merged_02['Neighborhood'], Houston_merged_02['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=3,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_houston_02)
    

# display map
map_houston_02

Based on the discussion above the candidate neighborhood for running a coffee shop would be in Cluster 3, 5, 1-0 and 1-4. Only the northside village in Cluster 5 has the relative high population density and household income and therefore this neighborhood would be recommended for running a coffee shop.

# Conclusion

Based on the available data, the venue categories in each neighborhood is analyzed and clustered. Further comparison with the density of population and household income is able to provide us a more insightful spatial analysis for the business problem. In this study, the running a coffee shop in Houston was demonstrated as an example for this kind of analysis. If more data (e.g. crime rate) is provided in the future a more detailed analysis could be done.